In [1]:
#Librerías
import pandas as pd
import matplotlib.pyplot as plt
import itertools
import numpy as np
import gc
from datetime import datetime
from tqdm import tqdm
from neuralprophet import NeuralProphet
import torch

#Configuración de parametros de Pandas para mejor visualización
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', None)
pd.set_option('display.precision', 3)
pd.set_option('plotting.backend', 'matplotlib') 
pd.options.mode.chained_assignment = None

c:\ProgramData\anaconda3\envs\neural_env2\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Importing plotly failed. Interactive plots will not work.
Importing plotly failed. Interactive plots will not work.


In [2]:
num_lags_principal=36
num_lags_otros=13

In [3]:
def percentage_safe(numerator: pd.Series, denominator: pd.Series, dtype='float32', fillna=None) -> pd.Series:
    """
    Calcula un porcentaje seguro como numerator / denominator.
    - Reemplaza divisiones por cero o NaN con NaN.
    - Opcionalmente convierte a float32.
    - Puede rellenar NaNs con `fillna`.
    """
    result = (numerator / denominator).mask((denominator == 0) | (denominator.isna()))
    if fillna is not None:
        result = result.fillna(fillna)
    return result.astype(dtype)

In [4]:
def reduce_mem_usage(df):
    """Itera por las columnas del DataFrame y modifica el tipo de datos para reducir uso de memoria."""
    start_mem = df.memory_usage().sum() / 1024**2
    print(f'Uso de memoria inicial del DataFrame: {start_mem:.2f} MB')

    for col in df.columns:
        col_type = df[col].dtype

        if pd.api.types.is_numeric_dtype(col_type):
            c_min = df[col].min()
            c_max = df[col].max()

            if pd.api.types.is_integer_dtype(col_type):
                if c_min >= np.iinfo(np.int8).min and c_max <= np.iinfo(np.int8).max:
                    df[col] = df[col].astype(np.int8)
                elif c_min >= np.iinfo(np.int16).min and c_max <= np.iinfo(np.int16).max:
                    df[col] = df[col].astype(np.int16)
                elif c_min >= np.iinfo(np.int32).min and c_max <= np.iinfo(np.int32).max:
                    df[col] = df[col].astype(np.int32)
                else:
                    df[col] = df[col].astype(np.int64)
            else:
                if c_min >= np.finfo(np.float16).min and c_max <= np.finfo(np.float16).max:
                    df[col] = df[col].astype(np.float16)
                elif c_min >= np.finfo(np.float32).min and c_max <= np.finfo(np.float32).max:
                    df[col] = df[col].astype(np.float32)
                else:
                    df[col] = df[col].astype(np.float64)
        else:
            # Sólo convertir a categoría si no lo es ya
            if not pd.api.types.is_categorical_dtype(df[col]):
                df[col] = df[col].astype('category')

    end_mem = df.memory_usage().sum() / 1024**2
    print(f'Uso de memoria final del DataFrame: {end_mem:.2f} MB')
    print(f'Memoria reducida en un {(100 * (start_mem - end_mem) / start_mem):.2f}%')
    return df

In [5]:
def clasificar_estado_producto(df: pd.DataFrame) -> None:
    """
    Clasifica el estado de los productos en un DataFrame basado en su ciclo de vida y ventas.

    La función evalúa una serie de condiciones y crea una nueva columna 'estado_producto'
    en el DataFrame proporcionado. La modificación se hace 'inplace'.

    Args:
        df (pd.DataFrame): El DataFrame que contiene los datos de los productos.
                           Debe incluir las columnas:
                           - 'meses_vida_producto'
                           - 'producto_crecimiento_ventas_suavizado'
                           - 'share_producto_en_categoria_suavizado'
    
    Returns:
        None: La función modifica el DataFrame directamente.
    """
    # Lista de condiciones en el orden de prioridad requerido
    condiciones = [
        (df['meses_vida_producto'] >= 0)& (df['meses_vida_producto'] <= 3),
        (df['producto_crecimiento_ventas_suavizado'] == 0),
        (df['producto_crecimiento_ventas_suavizado'] > 0.1) & (df['share_producto_en_categoria_suavizado'] > 0.1),
        (df['producto_crecimiento_ventas_suavizado'] < -0.1) & (df['share_producto_en_categoria_suavizado'] < -0.1)
    ]

    # Lista de resultados correspondientes a cada condición
    resultados = [
        'inicial',
        'sin ventas',
        'crecimiento',
        'contraccion'
    ]

    # El valor por defecto si ninguna condición se cumple es 'estable'
    df['estado_producto'] = np.select(condiciones, resultados, default='estable')


# Cargar Datos

In [6]:
#cargar csv
sellin = pd.read_csv('sell-in.txt', sep='\t')
productos = pd.read_csv('tb_productos.txt', sep='\t')
stocks = pd.read_csv('tb_stocks.txt', sep='\t')
#calidad_prediccion= pd.read_excel('comparar_predicciones.xlsx', sheet_name="comparacion")

# Armado inicial Dataset

In [7]:
#marcar todas las ventas como cliente_activo
sellin['cliente_activo']=1
sellin['producto_activo']=1

In [8]:
max_periodo=sellin['periodo'].max()
max_periodo

201912

In [9]:
vida_producto = sellin[sellin['producto_activo'] == 1].groupby('product_id')['periodo'].agg(
    inicio_vida_p='min', fin_vida_p='max'
).reset_index()

vida_cliente = sellin[sellin['cliente_activo'] == 1].groupby('customer_id')['periodo'].agg(
    inicio_vida_c='min'
).reset_index()

vida_cliente['fin_vida_c'] = max_periodo

In [10]:
#Paso 2: Cruce cliente-producto
cruce_cp = vida_cliente.merge(vida_producto, how='cross')  # Esto da un DataFrame con customer_id y product_id
cruce_cp.head(10)

customer_id  inicio_vida_c  fin_vida_c  product_id  inicio_vida_p  \
0        10001         201701      201912       20001         201701   
1        10001         201701      201912       20002         201701   
2        10001         201701      201912       20003         201701   
3        10001         201701      201912       20004         201701   
4        10001         201701      201912       20005         201701   
5        10001         201701      201912       20006         201701   
6        10001         201701      201912       20007         201701   
7        10001         201701      201912       20008         201701   
8        10001         201701      201912       20009         201701   
9        10001         201701      201912       20010         201701   

   fin_vida_p  
0      201912  
1      201912  
2      201912  
3      201912  
4      201912  
5      201912  
6      201912  
7      201912  
8      201912  
9      201912

In [11]:
#Paso 3: Crear periodos válidos
cruce_cp['inicio_vida'] = cruce_cp[['inicio_vida_c', 'inicio_vida_p']].max(axis=1)
cruce_cp['fin_vida'] = cruce_cp[['fin_vida_c', 'fin_vida_p']].min(axis=1)

# Filtrar combinaciones donde haya al menos un periodo posible
cruce_cp = cruce_cp[cruce_cp['inicio_vida'] <= cruce_cp['fin_vida']]

In [12]:
# Convertir las columnas a datetime primero
inicio_dt = pd.to_datetime(cruce_cp['inicio_vida'].astype(str), format='%Y%m')
fin_dt = pd.to_datetime(cruce_cp['fin_vida'].astype(str), format='%Y%m')

# Generar las listas de periodos como YYYYMM para cada par de fechas
cruce_cp['periodo'] = [
    [int(d.strftime('%Y%m')) for d in pd.date_range(start=ini, end=fin, freq='MS')]
    for ini, fin in zip(inicio_dt, fin_dt)
]

In [13]:
# Asegurarse de tener customer_id, product_id y periodo antes de explotar
combinaciones_validas = cruce_cp[['customer_id', 'product_id', 'periodo']].explode('periodo')

In [14]:
#Paso 5: Merge y completar faltantes
df_completo = combinaciones_validas.merge(sellin, on=['periodo', 'customer_id', 'product_id'], how='left')

In [15]:
#Paso 5: Merge y completar faltantes
df_completo = combinaciones_validas.merge(sellin, on=['periodo', 'customer_id', 'product_id'], how='left')

for col in ['cust_request_qty', 'cust_request_tn', 'tn']:
    df_completo[col] = df_completo[col].fillna(0)

df_completo['cliente_activo'] = df_completo['cliente_activo'].fillna(1)
df_completo['producto_activo'] = df_completo['producto_activo'].fillna(1)

In [16]:
df_completo.shape

(17173448, 9)

In [17]:
df_completo = df_completo.merge(
    cruce_cp[['customer_id', 'product_id', 'inicio_vida_c', 'fin_vida_c', 'inicio_vida_p', 'fin_vida_p', 'inicio_vida', 'fin_vida']],
    on=['customer_id', 'product_id'],
    how='left'
)
df_completo.head(5)

customer_id  product_id periodo  plan_precios_cuidados  cust_request_qty  \
0        10001       20001  201701                    0.0              11.0   
1        10001       20001  201702                    0.0              23.0   
2        10001       20001  201703                    0.0              33.0   
3        10001       20001  201704                    0.0               8.0   
4        10001       20001  201705                    0.0              15.0   

   cust_request_tn       tn  cliente_activo  producto_activo  inicio_vida_c  \
0           99.439   99.439             1.0              1.0         201701   
1          198.844  198.844             1.0              1.0         201701   
2           92.465   92.465             1.0              1.0         201701   
3           13.297   13.297             1.0              1.0         201701   
4          101.207  101.006             1.0              1.0         201701   

   fin_vida_c  inicio_vida_p  fin_vida_p  inicio_vida  fin_vida  
0      201912         201701      201912       201701    201912  
1      201912         201701      201912       201701    201912  
2      201912         201701      201912       201701    201912  
3      201912         201701      201912       201701    201912  
4      201912         201701      201912       201701    201912

In [18]:
# Convertimos los campos a datetime usando el primer día del mes
df_completo['fecha_periodo'] = pd.to_datetime(df_completo['periodo'].astype(str) + '01', format='%Y%m%d')
df_completo['fecha_inicio_c'] = pd.to_datetime(df_completo['inicio_vida_c'].astype(str) + '01', format='%Y%m%d')
df_completo['fecha_inicio_p'] = pd.to_datetime(df_completo['inicio_vida_p'].astype(str) + '01', format='%Y%m%d')

# Calculamos meses de vida +1 para que el primer mes dé 1
df_completo['meses_vida_cliente'] = (
    (df_completo['fecha_periodo'].dt.year - df_completo['fecha_inicio_c'].dt.year) * 12 +
    (df_completo['fecha_periodo'].dt.month - df_completo['fecha_inicio_c'].dt.month) + 1
)

df_completo['meses_vida_producto'] = (
    (df_completo['fecha_periodo'].dt.year - df_completo['fecha_inicio_p'].dt.year) * 12 +
    (df_completo['fecha_periodo'].dt.month - df_completo['fecha_inicio_p'].dt.month) + 1
)


In [19]:
df_completo.drop(columns=['fin_vida_c','fecha_periodo','inicio_vida','fin_vida','fecha_inicio_c','fecha_inicio_p'], inplace=True)

In [20]:
#Completar precios cuidados

plan_ref = sellin[['periodo', 'product_id', 'plan_precios_cuidados']].drop_duplicates()
plan_ref.head(5)


periodo  product_id  plan_precios_cuidados
0     201701       20524                      0
70    201701       20311                      0
171   201701       20654                      0
363   201701       21005                      0
390   201701       20974                      0

In [21]:
plan_ref['plan_precios_cuidados'].value_counts()


plan_precios_cuidados
0    30935
1      308
Name: count, dtype: int64

In [22]:
# Completar plan_precios_cuidados según referencia
df_full = df_completo.drop(columns=['plan_precios_cuidados'], inplace=True)  # eliminamos el incompleto si está

In [23]:
df_full = df_completo.merge(plan_ref, on=['periodo', 'product_id'], how='left')
df_full['plan_precios_cuidados'].value_counts()

plan_precios_cuidados
0.0    16853916
1.0      168063
Name: count, dtype: int64

In [24]:
df_full['plan_precios_cuidados']=df_full['plan_precios_cuidados'].fillna(0).astype(int)
df_full['plan_precios_cuidados'].value_counts()

plan_precios_cuidados
0    17005385
1      168063
Name: count, dtype: int64

In [25]:
del plan_ref
del combinaciones_validas
del cruce_cp
del df_completo
del sellin
gc.collect()

0

In [26]:
#unir en un solo dataset
df = (
    df_full
    .merge(productos, on='product_id', how='left')
    .merge(stocks, on=['product_id', 'periodo'], how='left')
)

In [27]:
df.drop(columns=['descripcion'], inplace=True)

# Genero los otros df

In [28]:
df_full= (
    df_full
    .merge(productos, on='product_id', how='left')
    .merge(stocks, on=['product_id', 'periodo'], how='left')
)

In [29]:
df_cliente = (
    df_full.groupby(['customer_id','periodo'])
      .agg(
          cliente_total_tn=('tn', 'sum'),
          cliente_avg_tn=('tn', 'mean'),
          cliente_std_tn=('tn', 'std'),
          cliente_min_tn=('tn', 'min'),
          cliente_max_tn=('tn', 'max'),
          cliente_productos_distintos=('product_id', 'nunique'),
      )
      .reset_index()
)

In [30]:
del df_full
gc.collect()
del stocks
gc.collect()

0

In [31]:
# Crear una fecha de inicio del mes
df['fecha'] = pd.to_datetime(df['periodo'], format="%Y%m")

# Obtener cantidad de días del mes original
#df['dias_en_mes'] = df['fecha'].dt.days_in_month

# Crear fechas para 1 y 2 meses posteriores
df['fecha_4'] = df['fecha'] + pd.DateOffset(months=4)
df['fecha_3'] = df['fecha'] + pd.DateOffset(months=3)

# Obtener días de cada uno de esos meses
df['dias_mes_4'] = df['fecha_4'].dt.days_in_month.astype(int)
df['dias_mes_3'] = df['fecha_3'].dt.days_in_month

# Agregar año, mes y trimestre
df['anio'] = df['fecha'].dt.year.astype(int)
df['mes'] = df['fecha'].dt.month.astype(int)
df['trimestre'] = df['fecha'].dt.quarter

# Limpiar columnas temporales
df.drop(columns=['fecha', 'fecha_4','fecha_3'], inplace=True)

In [32]:
#Defino mes outlier
df['outlier'] = (df['periodo'] == 201908).astype(int)
df['outlier-2'] = (df['periodo'] == 201906).astype(int)

In [33]:
df.head(5)

customer_id  product_id periodo  cust_request_qty  cust_request_tn  \
0        10001       20001  201701              11.0           99.439   
1        10001       20001  201702              23.0          198.844   
2        10001       20001  201703              33.0           92.465   
3        10001       20001  201704               8.0           13.297   
4        10001       20001  201705              15.0          101.207   

        tn  cliente_activo  producto_activo  inicio_vida_c  inicio_vida_p  \
0   99.439             1.0              1.0         201701         201701   
1  198.844             1.0              1.0         201701         201701   
2   92.465             1.0              1.0         201701         201701   
3   13.297             1.0              1.0         201701         201701   
4  101.006             1.0              1.0         201701         201701   

   fin_vida_p  meses_vida_cliente  meses_vida_producto  plan_precios_cuidados  \
0      201912                   1                    1                      0   
1      201912                   2                    2                      0   
2      201912                   3                    3                      0   
3      201912                   4                    4                      0   
4      201912                   5                    5                      0   

  cat1         cat2     cat3  brand  sku_size  stock_final  dias_mes_4  \
0   HC  ROPA LAVADO  Liquido  ARIEL    3000.0          NaN          31   
1   HC  ROPA LAVADO  Liquido  ARIEL    3000.0          NaN          30   
2   HC  ROPA LAVADO  Liquido  ARIEL    3000.0          NaN          31   
3   HC  ROPA LAVADO  Liquido  ARIEL    3000.0          NaN          31   
4   HC  ROPA LAVADO  Liquido  ARIEL    3000.0          NaN          30   

   dias_mes_3  anio  mes  trimestre  outlier  outlier-2  
0          30  2017    1          1        0          0  
1          31  2017    2          1        0          0  
2          30  2017    3          1        0          0  
3          31  2017    4          2        0          0  
4          31  2017    5          2        0          0

# LAGS serie principal

In [34]:
# ordenamiento previo:

df.sort_values(by=[ 'product_id', 'periodo'], inplace=True)

df.reset_index(drop=True, inplace=True)

# --- Generación de 36 Lags para la columna 'tn' (dejando NaNs) ---
print("\nGenerando 36 lags para la columna 'tn' (los NaNs serán preservados)...")
for i in range(1, 37): # Genera lags desde 1 hasta 36
    df[f'tn_lag_{i}'] = df.groupby(['product_id'])['tn'].shift(i)

print(f"Se han generado {len(range(1, num_lags_principal+1))} columnas de lag para 'tn'.")


Generando 36 lags para la columna 'tn' (los NaNs serán preservados)...
Se han generado 36 columnas de lag para 'tn'.


In [35]:
#for window in range(3, 13):  # de 3 a 12 inclusive
#    cols = ["tn"] + [f"tn_lag_{i}" for i in range(1, window)]
#    df[f"tn_media_movil_{window}"] = df[cols].mean(axis=1)

In [36]:
#Media móvil de 3 meses: tn + tn_lag_1 + tn_lag_2
df["tn_media_movil_3"] = df[["tn", "tn_lag_1", "tn_lag_2"]].mean(axis=1)

#Media móvil de 6 meses: tn + tn_lag_1 a tn_lag_5
df["tn_media_movil_6"] = df[["tn"] + [f"tn_lag_{i}" for i in range(1, 6)]].mean(axis=1)

#Media móvil de 6 meses: tn + tn_lag_1 a tn_lag_5
df["tn_media_movil_9"] = df[["tn"] + [f"tn_lag_{i}" for i in range(1, 9)]].mean(axis=1)

#Media móvil de 12 meses: tn + tn_lag_1 a tn_lag_11
df["tn_media_movil_12"] = df[["tn"] + [f"tn_lag_{i}" for i in range(1, 12)]].mean(axis=1)

In [37]:
#Desviación estándar de 3 meses: tn + tn_lag_1 + tn_lag_2
df["tn_std_movil_3"] = df[["tn", "tn_lag_1", "tn_lag_2"]].std(axis=1)

#Desviación estándar de 6 meses: tn + tn_lag_1 a tn_lag_5
df["tn_std_movil_6"] = df[["tn"] + [f"tn_lag_{i}" for i in range(1, 6)]].std(axis=1)

#Desviación estándar de 6 meses: tn + tn_lag_1 a tn_lag_5
df["tn_std_movil_9"] = df[["tn"] + [f"tn_lag_{i}" for i in range(1, 9)]].std(axis=1)

#Desviación estándar de 12 meses: tn + tn_lag_1 a tn_lag_11
df["tn_std_movil_12"] = df[["tn"] + [f"tn_lag_{i}" for i in range(1, 12)]].std(axis=1)

#for window in range(3, 13):  # de 3 a 12 inclusive
#    cols = ["tn"] + [f"tn_lag_{i}" for i in range(1, window)]
#    df[f"tn_std_movil_{window}"] = df[cols].std(axis=1)

In [38]:

# Mínimo de 3 meses: tn + tn_lag_1 + tn_lag_2
df["tn_min_movil_3"] = df[["tn", "tn_lag_1", "tn_lag_2"]].min(axis=1)

#Mínimo de 6 meses: tn + tn_lag_1 a tn_lag_5
df["tn_min_movil_6"] = df[["tn"] + [f"tn_lag_{i}" for i in range(1, 6)]].min(axis=1)

#Mínimo de 6 meses: tn + tn_lag_1 a tn_lag_5
df["tn_min_movil_9"] = df[["tn"] + [f"tn_lag_{i}" for i in range(1, 9)]].min(axis=1)

#Mínimo de 12 meses: tn + tn_lag_1 a tn_lag_11
df["tn_min_movil_12"] = df[["tn"] + [f"tn_lag_{i}" for i in range(1, 12)]].min(axis=1)

#for window in range(3, 13):
#    cols = ["tn"] + [f"tn_lag_{i}" for i in range(1, window)]
#    min_col = f"tn_min_movil_{window}"
#    delta_col = f"delta1_min_movil_{window}"

#    df[min_col] = df[cols].min(axis=1)
#    df[delta_col] = df['tn'] - df[min_col]



In [39]:
#Delta al promedio

df["delta_media_movil_12"]=df['tn']-df["tn_media_movil_12"]
df["delta_media_movil_3"]=df['tn']-df["tn_media_movil_3"]
df["delta_media_movil_6"]=df['tn']-df["tn_media_movil_6"]
df["delta_media_movil_9"]=df['tn']-df["tn_media_movil_9"]


df["delta_std_movil_12"]=df['tn']-df["tn_std_movil_12"]
df["delta_std_movil_3"]=df['tn']-df["tn_std_movil_3"]
df["delta_std_movil_6"]=df['tn']-df["tn_std_movil_6"]
df["delta_std_movil_9"]=df['tn']-df["tn_std_movil_9"]

df["delta_min_movil_12"]=df['tn']-df["tn_min_movil_12"]
df["delta_min_movil_3"]=df['tn']-df["tn_min_movil_3"]
df["delta_min_movil_6"]=df['tn']-df["tn_min_movil_6"]
df["delta_min_movil_9"]=df['tn']-df["tn_min_movil_9"]


#for window in range(3, 13):
#    media_col = f"tn_media_movil_{window}"
#    delta_col = f"delta_media_movil_{window}"
#    df[delta_col] = df['tn'] - df[media_col]

In [40]:
# --- Generar las diferencias (delta_tn_X) para todos los lags (dejando NaNs) ---
print("\nGenerando columnas de diferencia (delta_tn_X) (los NaNs serán preservados)...")
for i in range(1, num_lags_principal+1): 
    df[f'delta_tn_{i}'] = df['tn'] - df[f'tn_lag_{i}']


Generando columnas de diferencia (delta_tn_X) (los NaNs serán preservados)...


WARNING - (py.warnings._showwarnmsg) - C:\Users\diana\AppData\Local\Temp\ipykernel_16316\1356617918.py:4: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'delta_tn_{i}'] = df['tn'] - df[f'tn_lag_{i}']

WARNING - (py.warnings._showwarnmsg) - C:\Users\diana\AppData\Local\Temp\ipykernel_16316\1356617918.py:4: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'delta_tn_{i}'] = df['tn'] - df[f'tn_lag_{i}']

WARNING - (py.warnings._showwarnmsg) - C:\Users\diana\AppData\Local\Temp\ipykernel_16316\1356617918.py:4: PerformanceWarning: 

# serie cliente

In [41]:
# Asegurate de que esté ordenado por periodo
df_cliente = df_cliente.sort_values('periodo').reset_index(drop=True)


In [42]:
for lag in range(1, num_lags_otros + 1):
    # Creamos la columna de lag con un nombre consistente
    lag_col = f'cliente_total_tn_lag_{lag}'
    df_cliente[lag_col] = df_cliente['cliente_total_tn'].shift(lag)
    
    # Calculamos la diferencia entre el valor original y el valor en el lag
    df_cliente[f'cliente_total_tn_diff_{lag}'] = df_cliente['cliente_total_tn'] - df_cliente[lag_col]

In [43]:
df_cliente.head()

customer_id  periodo  cliente_total_tn  cliente_avg_tn  cliente_std_tn  \
0        10001   201701          2543.899           3.241           9.723   
1        10029   201701           113.336           0.144           0.281   
2        10494   201701            20.302           0.026           0.459   
3        10263   201701             0.911           0.001           0.031   
4        10262   201701            11.019           0.014           0.036   

   cliente_min_tn  cliente_max_tn  cliente_productos_distintos  \
0             0.0         100.213                          785   
1             0.0           2.143                          785   
2             0.0           9.022                          785   
3             0.0           0.874                          785   
4             0.0           0.415                          785   

   cliente_total_tn_lag_1  cliente_total_tn_diff_1  cliente_total_tn_lag_2  \
0                     NaN                      NaN                     NaN   
1                2543.899                -2430.564                     NaN   
2                 113.336                  -93.033                2543.899   
3                  20.302                  -19.392                 113.336   
4                   0.911                   10.109                  20.302   

   cliente_total_tn_diff_2  cliente_total_tn_lag_3  cliente_total_tn_diff_3  \
0                      NaN                     NaN                      NaN   
1                      NaN                     NaN                      NaN   
2                -2523.597                     NaN                      NaN   
3                 -112.425                2543.899                -2542.989   
4                   -9.283                 113.336                 -102.316   

   cliente_total_tn_lag_4  cliente_total_tn_diff_4  cliente_total_tn_lag_5  \
0                     NaN                      NaN                     NaN   
1                     NaN                      NaN                     NaN   
2                     NaN                      NaN                     NaN   
3                     NaN                      NaN                     NaN   
4                2543.899                 -2532.88                     NaN   

   cliente_total_tn_diff_5  cliente_total_tn_lag_6  cliente_total_tn_diff_6  \
0                      NaN                     NaN                      NaN   
1                      NaN                     NaN                      NaN   
2                      NaN                     NaN                      NaN   
3                      NaN                     NaN                      NaN   
4                      NaN                     NaN                      NaN   

   cliente_total_tn_lag_7  cliente_total_tn_diff_7  cliente_total_tn_lag_8  \
0                     NaN                      NaN                     NaN   
1                     NaN                      NaN                     NaN   
2                     NaN                      NaN                     NaN   
3                     NaN                      NaN                     NaN   
4                     NaN                      NaN                     NaN   

   cliente_total_tn_diff_8  cliente_total_tn_lag_9  cliente_total_tn_diff_9  \
0                      NaN                     NaN                      NaN   
1                      NaN                     NaN                      NaN   
2                      NaN                     NaN                      NaN   
3                      NaN                     NaN                      NaN   
4                      NaN                     NaN                      NaN   

   cliente_total_tn_lag_10  cliente_total_tn_diff_10  cliente_total_tn_lag_11  \
0                      NaN                       NaN                      NaN   
1                      NaN                       NaN                      NaN   
2                      NaN                       NaN                

In [44]:
    
for window in [3, 6, 12]:
    df_cliente[f'cliente_total_tn_ma_{window}'] = (
        df_cliente['cliente_total_tn']
        .transform(lambda x: x.shift(1).rolling(window=window, min_periods=1).mean())
    )

In [45]:
for window in [3, 6, 12]:
    df_cliente[f'cliente_total_tn_min_{window}'] = (
        df_cliente['cliente_total_tn']
        .transform(lambda x: x.shift(1).rolling(window=window, min_periods=1).min())
    )

In [46]:
for window in [3, 6, 12]:
    df_cliente[f'cliente_total_tn_std_{window}'] = (
        df_cliente['cliente_total_tn']
        .transform(lambda x: x.shift(1).rolling(window=window, min_periods=1).std())
    )

In [47]:
df_cliente['cliente_total_delta_media_movil_3']=df_cliente['cliente_total_tn']-df_cliente['cliente_total_tn_ma_3']
df_cliente['cliente_total_delta_media_movil_6']=df_cliente['cliente_total_tn']-df_cliente['cliente_total_tn_ma_6']
df_cliente['cliente_total_delta_media_movil_12']=df_cliente['cliente_total_tn']-df_cliente['cliente_total_tn_ma_12']

In [48]:
df_cliente['cliente_total_delta_min_movil_3']=df_cliente['cliente_total_tn']-df_cliente['cliente_total_tn_min_3']
df_cliente['cliente_total_delta_min_movil_6']=df_cliente['cliente_total_tn']-df_cliente['cliente_total_tn_min_6']
df_cliente['cliente_total_delta_min_movil_12']=df_cliente['cliente_total_tn']-df_cliente['cliente_total_tn_min_12']

In [49]:
df_cliente['cliente_total_delta_std_movil_3']=df_cliente['cliente_total_tn']-df_cliente['cliente_total_tn_std_3']
df_cliente['cliente_total_delta_std_movil_']=df_cliente['cliente_total_tn']-df_cliente['cliente_total_tn_std_6']
df_cliente['cliente_total_delta_std_movil_12']=df_cliente['cliente_total_tn']-df_cliente['cliente_total_tn_std_12']

## Neural Prophet Cliente

In [50]:
df_cliente['ds'] = pd.to_datetime(df_cliente['periodo'].astype(str), format='%Y%m')
df_cliente['y']=df_cliente['cliente_total_tn'].astype('float32')

In [51]:
df_cliente.head(5)

customer_id  periodo  cliente_total_tn  cliente_avg_tn  cliente_std_tn  \
0        10001   201701          2543.899           3.241           9.723   
1        10029   201701           113.336           0.144           0.281   
2        10494   201701            20.302           0.026           0.459   
3        10263   201701             0.911           0.001           0.031   
4        10262   201701            11.019           0.014           0.036   

   cliente_min_tn  cliente_max_tn  cliente_productos_distintos  \
0             0.0         100.213                          785   
1             0.0           2.143                          785   
2             0.0           9.022                          785   
3             0.0           0.874                          785   
4             0.0           0.415                          785   

   cliente_total_tn_lag_1  cliente_total_tn_diff_1  cliente_total_tn_lag_2  \
0                     NaN                      NaN                     NaN   
1                2543.899                -2430.564                     NaN   
2                 113.336                  -93.033                2543.899   
3                  20.302                  -19.392                 113.336   
4                   0.911                   10.109                  20.302   

   cliente_total_tn_diff_2  cliente_total_tn_lag_3  cliente_total_tn_diff_3  \
0                      NaN                     NaN                      NaN   
1                      NaN                     NaN                      NaN   
2                -2523.597                     NaN                      NaN   
3                 -112.425                2543.899                -2542.989   
4                   -9.283                 113.336                 -102.316   

   cliente_total_tn_lag_4  cliente_total_tn_diff_4  cliente_total_tn_lag_5  \
0                     NaN                      NaN                     NaN   
1                     NaN                      NaN                     NaN   
2                     NaN                      NaN                     NaN   
3                     NaN                      NaN                     NaN   
4                2543.899                 -2532.88                     NaN   

   cliente_total_tn_diff_5  cliente_total_tn_lag_6  cliente_total_tn_diff_6  \
0                      NaN                     NaN                      NaN   
1                      NaN                     NaN                      NaN   
2                      NaN                     NaN                      NaN   
3                      NaN                     NaN                      NaN   
4                      NaN                     NaN                      NaN   

   cliente_total_tn_lag_7  cliente_total_tn_diff_7  cliente_total_tn_lag_8  \
0                     NaN                      NaN                     NaN   
1                     NaN                      NaN                     NaN   
2                     NaN                      NaN                     NaN   
3                     NaN                      NaN                     NaN   
4                     NaN                      NaN                     NaN   

   cliente_total_tn_diff_8  cliente_total_tn_lag_9  cliente_total_tn_diff_9  \
0                      NaN                     NaN                      NaN   
1                      NaN                     NaN                      NaN   
2                      NaN                     NaN                      NaN   
3                      NaN                     NaN                      NaN   
4                      NaN                     NaN                      NaN   

   cliente_total_tn_lag_10  cliente_total_tn_diff_10  cliente_total_tn_lag_11  \
0                      NaN                       NaN                      NaN   
1                      NaN                       NaN                      NaN   
2                      NaN                       NaN                

In [52]:
import torch
print(torch.__version__)


2.5.1+cpu


In [53]:
# Inicializamos la variable como un DataFrame vacío para evitar el AttributeError
df_resultado_final = pd.DataFrame()

df_prophet = df_cliente[['ds', 'y']].copy()

# Listas para almacenar resultados y errores
df_all = []
errores_np = []

# Iterar sobre cada 'categoria' única
# La variable 'categoria_id' contendrá el identificador único de la categoría (ej: "A_B_C")
# La variable 'grupo' contendrá el sub-DataFrame para esa categoría
for customer_id, grupo in tqdm(df_cliente.groupby('customer_id'), desc="Procesando clientes"):
    
    # Seleccionar solo las columnas necesarias para NeuralProphet
    grupo_limpio = grupo[['ds', 'y']].copy()

    # Filtro para series muy cortas o sin variabilidad (buena práctica)
    if len(grupo_limpio) < 12 or grupo_limpio['y'].nunique() < 3:
        continue

    try:
        # Inicializar el modelo
        m = NeuralProphet(
            yearly_seasonality=True,
            weekly_seasonality=False, # No aplica para datos mensuales
            daily_seasonality=False,
            #n_forecasts=1, # Especifica el horizonte de predicción si lo necesitas
            n_lags=12 # Recomiendo añadir lags para mejorar el modelo AR
        )
        
        # Ajustar el modelo con los datos de la categoría actual
        # freq='M' es para frecuencia mensual al final del mes. 'MS' es al inicio.
        m.fit(grupo_limpio, freq='MS') 
        
        # Predecir sobre el mismo dataframe para extraer componentes (tendencia, estacionalidad)
        pred = m.predict(grupo_limpio)

        # Añadir la columna 'categoria' para poder identificar los resultados
        pred['customer_id'] = customer_id
        
        # Guardar las columnas relevantes. 'yearly' es la estacionalidad anual.
        df_all.append(pred[['ds', 'customer_id', 'trend', 'season_yearly']])
    
    except Exception as e:
        # Registrar el ID de la categoría que falló y el mensaje de error
        errores_np.append((customer_id, str(e)))
        continue

# --- 3. Consolidación de Resultados ---

# Solo si se procesó al menos una categoría con éxito
if df_all:
    # Concatenar todos los dataframes de predicciones en uno solo
    df_np_feats = pd.concat(df_all, ignore_index=True)

    # Unir las nuevas características (trend, season_yearly) al dataframe original
    # Usamos 'on' porque los nombres de las columnas ('ds', 'categoria') son los mismos en ambos dataframes
    #df_final  = df_categoria.merge(df_np_feats, on=['ds', 'categoria'], how='left')

    print("✅ Proceso completado.")
    print(f"Se generaron características para {len(df_np_feats['customer_id'].unique())} clientes.")
    
    # Opcional: limpiar columnas que ya no necesites
    # df_final.drop(columns=['y'], inplace=True)

else:
    print("⚠️ No se pudo procesar ninguna categoría. La lista de resultados está vacía.")


# --- 4. Reporte de Errores ---
if errores_np:
    print(f"\n⚠️ Fallaron {len(errores_np)} categorías al entrenar NeuralProphet.")
    # Imprimir los primeros 5 errores para diagnóstico
    for cat_id, msg in errores_np[:5]:
        print(f"  - cliente={customer_id} → {msg[:120]}...")
else:
    print("✅ Todas las series se procesaron sin errores.")

if len(df_prophet) < 12 or df_prophet['y'].nunique() < 3:
    print(f"⚠️ La serie es muy corta o no tiene suficiente variabilidad para ser procesada.")
else:
    try:
        print(f"✅ Procesando la serie...")
        m = NeuralProphet(
            yearly_seasonality=True,
            weekly_seasonality=False,
            daily_seasonality=False,
            n_lags=12
        )
        # El error 'Weights only load failed' se previene con la línea de torch.serialization añadida arriba
        m.fit(df_prophet, freq='MS')
        
        predicciones = m.predict(df_prophet)
        componentes = predicciones[['ds', 'trend', 'season_yearly']]
        
        # Esta línea ahora se ejecutará correctamente
        df_resultado_final = pd.merge(df_prophet, componentes, on='ds', how='left')
        
        print("\n✅ Proceso completado con éxito.")

    except Exception as e:
        print(f"\n❌ Ocurrió un error al procesar la serie:")
        print(e)

# Verificamos si el DataFrame no está vacío en lugar de si es None
if not df_resultado_final.empty:
    print("\n--- Vista previa del resultado final ---")
    print(df_resultado_final.head())
else:
    print("\n--- No se generó ningún resultado final debido a un error o datos insuficientes. ---")

Procesando clientes:   0%|          | 0/597 [00:00<?, ?it/s]INFO - (NP.forecaster.fit) - When Global modeling with local normalization, metrics are displayed in normalized scale.
WARNING - (py.warnings._showwarnmsg) - c:\ProgramData\anaconda3\envs\neural_env2\lib\site-packages\neuralprophet\df_utils.py:463: FutureWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  if df.groupby("ID").apply(lambda x: x.duplicated("ds").any()).any():

WARNING - (py.warnings._showwarnmsg) - c:\ProgramData\anaconda3\envs\neural_env2\lib\site-packages\neuralprophet\df_utils.py:1149: FutureWarning: Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.
  converted_ds = p

Training: |          | 0/? [00:00<?, ?it/s]

WARNING - (NP.config.set_lr_finder_args) - Learning rate finder: The number of batches (3) is too small than the required number                     for the learning rate finder (203). The results might not be optimal.
WARNING - (py.warnings._showwarnmsg) - c:\ProgramData\anaconda3\envs\neural_env2\lib\site-packages\pytorch_lightning\utilities\data.py:79: Trying to infer the `batch_size` from an ambiguous collection. The batch size we found is 8. To avoid any miscalculations, use `self.log(..., batch_size=batch_size)`.

Finding best initial lr: 100%|██████████| 203/203 [00:02<00:00, 91.60it/s] 


Training: |          | 0/? [00:15<?, ?it/s, v_num=551, train_loss=0.0213, reg_loss=0.000, MAE=309.0, RMSE=391.0, Loss=0.0213, RegLoss=0.000]  

WARNING - (py.warnings._showwarnmsg) - c:\ProgramData\anaconda3\envs\neural_env2\lib\site-packages\neuralprophet\df_utils.py:1149: FutureWarning: Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.
  converted_ds = pd.to_datetime(ds_col, utc=True).view(dtype=np.int64)



...

WARNING - (py.warnings._showwarnmsg) - c:\ProgramData\anaconda3\envs\neural_env2\lib\site-packages\neuralprophet\df_utils.py:1149: FutureWarning: Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.
  converted_ds = pd.to_datetime(ds_col, utc=True).view(dtype=np.int64)

INFO - (NP.df_utils._infer_frequency) - Major frequency MS corresponds to [97.222]% of the data.
WARNING - (py.warnings._showwarnmsg) - c:\ProgramData\anaconda3\envs\neural_env2\lib\site-packages\neuralprophet\df_utils.py:1149: FutureWarning: Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.
  converted_ds = pd.to_datetime(ds_col, utc=True).view(dtype=np.int64)

WARNING - (py.warnings._showwarnmsg) - c:\ProgramData\anaconda3\envs\neural_env2\lib\site-packages\neuralprophet\df_utils.py:1149: FutureWarning: Series.view is deprecated and will be removed in a future version. Use ``astype

Predicting DataLoader 0: 100%|██████████| 1/1 [00:00<00:00, 76.88it/s]

INFO - (NP.df_utils.return_df_in_original_format) - Returning df with no ID column
Procesando clientes: 100%|██████████| 597/597 [2:51:17<00:00, 17.22s/it]


INFO - (NP.forecaster.fit) - When Global modeling with local normalization, metrics are displayed in normalized scale.
WARNING - (py.warnings._showwarnmsg) - c:\ProgramData\anaconda3\envs\neural_env2\lib\site-packages\neuralprophet\df_utils.py:463: FutureWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  if df.groupby("ID").apply(lambda x: x.duplicated("ds").any()).any():



✅ Proceso completado.
Se generaron características para 549 clientes.

⚠️ Fallaron 1 categorías al entrenar NeuralProphet.
  - cliente=10637 → Dataframe has less than n_forecasts + n_lags rows. Forecasting not possible. Please either use a larger dataset, or adju...
✅ Procesando la serie...

❌ Ocurrió un error al procesar la serie:
Column ds has duplicate values. Please remove duplicates.

--- No se generó ningún resultado final debido a un error o datos insuficientes. ---


In [54]:
df_np_feats.tail(5)

ds  customer_id  trend  season_yearly
19040 2019-08-01        10635 -0.005      3.626e-03
19041 2019-09-01        10635 -0.005     -8.454e-04
19042 2019-10-01        10635 -0.005      4.084e-03
19043 2019-11-01        10635 -0.006     -3.430e-03
19044 2019-12-01        10635 -0.006      1.109e-03

In [58]:
df_cliente.shape

(19555, 54)

In [60]:
df_cliente = (
    df_cliente
    .merge(df_np_feats, on=['ds','customer_id'], how='left')
)

In [ ]:
df_cliente = df_cliente.rename(columns={'trend': 'cliente_trend','season_yearly': 'cliente_season_yearly'})


In [62]:
df_cliente.shape

(19555, 56)

In [63]:
df_cliente.tail(12)

customer_id  periodo  cliente_total_tn  cliente_avg_tn  cliente_std_tn  \
19543        10513   201912             0.000       0.000e+00           0.000   
19544        10051   201912            58.468       6.307e-02           0.322   
19545        10227   201912             2.481       2.676e-03           0.016   
19546        10228   201912             3.621       3.906e-03           0.034   
19547        10512   201912             0.153       1.649e-04           0.005   
19548        10229   201912             0.000       0.000e+00           0.000   
19549        10511   201912             0.560       6.037e-04           0.018   
19550        10050   201912           117.361       1.266e-01           0.961   
19551        10510   201912             0.000       0.000e+00           0.000   
19552        10230   201912             0.000       0.000e+00           0.000   
19553        10226   201912             1.186       1.280e-03           0.015   
19554        10637   201912             0.000       0.000e+00           0.000   

       cliente_min_tn  cliente_max_tn  cliente_productos_distintos  \
19543             0.0           0.000                          927   
19544             0.0           5.154                          927   
19545             0.0           0.236                          927   
19546             0.0           0.559                          927   
19547             0.0           0.153                          927   
19548             0.0           0.000                          927   
19549             0.0           0.560                          927   
19550             0.0          18.673                          927   
19551             0.0           0.000                          927   
19552             0.0           0.000                          927   
19553             0.0           0.262                          927   
19554             0.0           0.000                          927   

       cliente_total_tn_lag_1  cliente_total_tn_diff_1  \
19543                  14.401                  -14.401   
19544                   0.000                   58.468   
19545                  58.468                  -55.987   
19546                   2.481                    1.140   
19547                   3.621                   -3.468   
19548                   0.153                   -0.153   
19549                   0.000                    0.560   
19550                   0.560                  116.801   
19551                 117.361                 -117.361   
19552                   0.000                    0.000   
19553                   0.000                    1.186   
19554                   1.186                   -1.186   

       cliente_total_tn_lag_2  cliente_total_tn_diff_2  \
19543                   4.722                   -4.722   
19544                  14.401                   44.067   
19545                   0.000                    2.481   
19546                  58.468                  -54.847   
19547                   2.481                   -2.328   
19548                   3.621                   -3.621   
19549                   0.153                    0.407   
19550                   0.000                  117.361   
19551                   0.560                   -0.560   
19552                 117.361                 -117.361   
19553                   0.000                    1.186   
19554                   0.000                    0.000   

       cliente_total_tn_lag_3  cliente_total_tn_diff_3  \
19543                  12.855                  -12.855   
19544                   4.722                   53.746   
19545                  14.401                  -11.920   
19546                   0.000                    3.621   
19547                  58.468                  -58.315   
19548                   2.481                   -2.481   
19549                   3.621                   -3.061   
19550                   0.153                  117.208   
19551     

In [ ]:
del df_cliente['y']
del df_cliente['ds']
del df_np_feats
del df_prophet
gc.collect()


NameError: name 'predicciones' is not defined

## union con otros dataset

In [66]:
df_cliente = reduce_mem_usage(df_cliente)


Uso de memoria inicial del DataFrame: 7.91 MB
Uso de memoria final del DataFrame: 2.05 MB
Memoria reducida en un 74.06%


In [68]:
df = reduce_mem_usage(df)

Uso de memoria inicial del DataFrame: 12152.39 MB


WARNING - (py.warnings._showwarnmsg) - C:\Users\diana\AppData\Local\Temp\ipykernel_16316\3492438140.py:31: DeprecationWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, pd.CategoricalDtype) instead
  if not pd.api.types.is_categorical_dtype(df[col]):

WARNING - (py.warnings._showwarnmsg) - C:\Users\diana\AppData\Local\Temp\ipykernel_16316\3492438140.py:31: DeprecationWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, pd.CategoricalDtype) instead
  if not pd.api.types.is_categorical_dtype(df[col]):



Uso de memoria final del DataFrame: 3897.94 MB
Memoria reducida en un 67.92%


In [69]:
gc.collect()

478

In [70]:
df.shape

(17173448, 123)

In [73]:
df = df.merge(
    df_cliente,
    on=['periodo','customer_id'],
    how='left'
)

In [74]:
df.shape

(17173448, 175)

In [75]:
del df_cliente
gc.collect()

0

In [76]:
df = reduce_mem_usage(df)
gc.collect()

Uso de memoria inicial del DataFrame: 5715.88 MB


WARNING - (py.warnings._showwarnmsg) - C:\Users\diana\AppData\Local\Temp\ipykernel_16316\3492438140.py:31: DeprecationWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, pd.CategoricalDtype) instead
  if not pd.api.types.is_categorical_dtype(df[col]):



Uso de memoria final del DataFrame: 5650.37 MB
Memoria reducida en un 1.15%


0

In [77]:
df.shape

(17173448, 175)

# Clase

In [78]:
#Definir clase
# Ordenar por grupo y tiempo antes del shift negativo
df.sort_values([ 'product_id', 'periodo'], inplace=True)
df.reset_index(drop=True, inplace=True)

# Crear columna con el valor de tn dentro de dos períodos futuros
df['tn_+_2'] = df.groupby(['product_id'])['tn'].shift(-2)

# Calcular diferencia (puede usarse como proxy de tendencia)
df['clase'] = df['tn_+_2'] - df['tn'].fillna(0)

# Limpiar columna temporal
del df['tn_+_2']
df['clase'] = df['clase'].fillna(0)

WARNING - (py.warnings._showwarnmsg) - C:\Users\diana\AppData\Local\Temp\ipykernel_16316\1709805598.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['tn_+_2'] = df.groupby(['product_id'])['tn'].shift(-2)

WARNING - (py.warnings._showwarnmsg) - C:\Users\diana\AppData\Local\Temp\ipykernel_16316\1709805598.py:10: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['clase'] = df['tn_+_2'] - df['tn'].fillna(0)



In [79]:
df = reduce_mem_usage(df)
gc.collect()

Uso de memoria inicial del DataFrame: 5683.13 MB


WARNING - (py.warnings._showwarnmsg) - C:\Users\diana\AppData\Local\Temp\ipykernel_16316\3492438140.py:31: DeprecationWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, pd.CategoricalDtype) instead
  if not pd.api.types.is_categorical_dtype(df[col]):



Uso de memoria final del DataFrame: 5683.13 MB
Memoria reducida en un 0.00%


0

In [80]:
gc.collect()

0

# Exportar 

In [81]:
df['periodo'] = df['periodo'].astype(str).str.replace('-', '').astype(int)

In [99]:
df = reduce_mem_usage(df)
gc.collect()

Uso de memoria inicial del DataFrame: 5797.77 MB


WARNING - (py.warnings._showwarnmsg) - C:\Users\diana\AppData\Local\Temp\ipykernel_16316\3492438140.py:31: DeprecationWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, pd.CategoricalDtype) instead
  if not pd.api.types.is_categorical_dtype(df[col]):



Uso de memoria final del DataFrame: 5666.75 MB
Memoria reducida en un 2.26%


1844

In [83]:
df['cust_request_qty']=df['cust_request_qty'].astype('Int64')
#df['cust_request_qty']=df['cust_request_qty'].astype('Int64')



In [101]:
df.to_parquet('cliente_producto_base.parquet', index=False)

In [102]:
#df_train = df[~df['periodo'].isin([201911, 201912])]
df_train = df.query("periodo != 201911 and periodo != 201912")

df_train.to_parquet('0_train_cliente_producto.parquet', index=False)
print(f"DataFrame de entrenamiento guardado en 'train.parquet' con {len(df_train)} filas.")

# --- 3. Preparar y guardar el DataFrame de predicción en Parquet ---
# Seleccionamos los periodos 201911 y 201912 para el conjunto de predicción.
# Eliminamos la columna 'clase' ya que no será necesaria para la predicción.
# Finalmente, guardamos este DataFrame en un archivo Parquet.
df_predecir = df[df['periodo'].isin([201911, 201912])].copy() # Usar .copy() para evitar SettingWithCopyWarning
df_predecir.drop(columns=['clase'], inplace=True)
df_predecir.to_parquet('0_predecir_cliente_producto.parquet', index=False)
print(f"DataFrame para predicción guardado en 'predecir.parquet' con {len(df_predecir)} filas.")

DataFrame de entrenamiento guardado en 'train.parquet' con 16058944 filas.
DataFrame para predicción guardado en 'predecir.parquet' con 1114504 filas.


In [104]:
df.shape

(17173448, 176)

In [107]:
df.head(10000).to_excel('0_cliente_producto_base.xlsx',sheet_name='hoja1',index=False)